<a href="https://colab.research.google.com/github/ChiragBellara/Video-Translation-Using-Deep-Learning/blob/silbunsa-patch-1/TextToSpeech.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

This module would be used for converting Text to Speech. I have currently used suno-bark(https://github.com/suno-ai/bark) as it uses transformer for the voice and supports 13 languages. As a video can have lengthy speech I have used nltk for splitting them into sentences. Initially I am taking script.txt as the speech that needs to be converted and saving it as a tts.wav file.

This module needs to work as an API getting the speech and outputting the audio file for desired language.

In [1]:
!pip install git+https://github.com/suno-ai/bark.git

  Cloning https://github.com/suno-ai/bark.git to /tmp/pip-req-build-a5mmqcip
  Running command git clone --filter=blob:none --quiet https://github.com/suno-ai/bark.git /tmp/pip-req-build-a5mmqcip
  Resolved https://github.com/suno-ai/bark.git to commit 773624d26db84278a55aacae9a16d7b25fbccab8
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.8/135.8 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 18.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 24.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 44.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 70.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.3/11.3 MB 79.9 MB/s eta 0:00:00
    

In [2]:
!pip install git+https://github.com/huggingface/transformers.git

  Cloning https://github.com/huggingface/transformers.git to /tmp/pip-req-build-gamjbw6_
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/transformers.git /tmp/pip-req-build-gamjbw6_
  Resolved https://github.com/huggingface/transformers.git to commit 093848d3ccf3884caf048718b6bae833da0edb94
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for transformers: filename=transformers-4.35.0.dev0-py3-none-any.whl size=7817578 sha256=0667138b64c5212293e3cef49bb3cf8afd07d57f1e689c063a6a33dcd87f568f
  Stored in directory: /tmp/pip-ephem-wheel-cache-fvc9zii4/wheels/e7/9c/5b/e1a9c8007c343041e61cc484433d512ea9274272e3fcbe7c16
Successfully built transformers
  Attempting uninstall: transformers
    Found existing installation: transformers 4.34.1
    Uninstalling transformers-4.34.1:
      Successfully uninstalled transformers-4.34.1


In [42]:
from bark import SAMPLE_RATE, generate_audio, preload_models
from scipy.io.wavfile import write as write_wav
from IPython.display import Audio
import scipy
# download and load all models
preload_models()


In [43]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
import nltk  # we'll use this to split into sentences
import numpy as np

nltk.download('punkt')
from bark.generation import (
    generate_text_semantic,
    preload_models,
)
from bark.api import semantic_to_waveform
from bark import generate_audio, SAMPLE_RATE



[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [44]:
script_file = "script.txt"
with open(script_file, "r") as file:
  script = file.read()
script.replace("\n", " ").strip()


sentences = nltk.sent_tokenize(script)
SPEAKER = "v2/hi_speaker_6"
silence = np.zeros(int(0.25 * SAMPLE_RATE))  # quarter second of silence

GEN_TEMP = 0.6
SPEAKER = "v2/hi_speaker_3"
silence = np.zeros(int(0.25 * SAMPLE_RATE))  # quarter second of silence

pieces = []
for sentence in sentences:
    semantic_tokens = generate_text_semantic(
        sentence,
        history_prompt=SPEAKER,
        temp=GEN_TEMP,
        min_eos_p=0.05,  # this controls how likely the generation is to end
    )

    audio_array = semantic_to_waveform(semantic_tokens, history_prompt=SPEAKER,)
    pieces += [audio_array, silence.copy()]

Audio(np.concatenate(pieces), rate=SAMPLE_RATE)
#scipy.io.wavfile.write("text_speech.wav", rate=SAMPLE_RATE, data=audio_array)

100%|██████████| 32/32 [00:29<00:00,  1.07it/s]
